In [1]:
from learning_lib.nn.monitoring.activations import ActivationMonitor
from learning_lib.nn.monitoring.weights import WeightMonitor
from learning_lib.nn.monitoring.gradient import LossGradientMonitor, LossGradientNormMonitor
from learning_lib.nn.monitoring.loss import LossMonitor

from learning_lib.nn.ffnn import FFNN
from learning_lib.nn.cnn import CNN
from learning_lib.nn.nn_base_class import NN

from sklearn.manifold import TSNE
import pandas as pd
import numpy as np
import tensorflow as tf
from tensorflow.examples.tutorials.mnist import input_data

import plotly.offline as plotly
import plotly.graph_objs as go
from PIL import Image

/home/fwang/anaconda3/lib/python3.6/site-packages/h5py/__init__.py:34: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters


In [2]:
%matplotlib inline
plotly.init_notebook_mode(connected=True)

# Data

In [3]:
dataset = input_data.read_data_sets("MNIST_data/", one_hot=True)
test_data = dataset.test.next_batch(1000000)
train_data = dataset.train.next_batch(1000000)
test_in = test_data[0] - train_data[0].mean()
train_in = train_data[0] - train_data[0].mean()
test_labels = test_data[1]
train_labels = train_data[1]

Extracting MNIST_data/train-images-idx3-ubyte.gz
Extracting MNIST_data/train-labels-idx1-ubyte.gz
Extracting MNIST_data/t10k-images-idx3-ubyte.gz
Extracting MNIST_data/t10k-labels-idx1-ubyte.gz


# Simple Autoencoder

In [152]:
d = tf.data.Dataset.from_tensor_slices((train_in, train_in))
d = d.repeat(50)
d = d.batch(300)
iterator = d.make_initializable_iterator()
pipe_out = iterator.get_next()

In [153]:
lc = [
    784,
    {
        'n_nodes': 64, 'activation': tf.tanh, 'init_weight_mean': 0.0, 'init_weight_stddev': 0.01,
        'init_bias_mean': 0.0, 'init_bias_stddev': 0.01
    },
    {
        'n_nodes': 64, 'activation': tf.tanh, 'init_weight_mean': 0.0, 'init_weight_stddev': 0.01,
        'init_bias_mean': 0.0, 'init_bias_stddev': 0.01
    },
    {
        'n_nodes': 64, 'activation': tf.tanh, 'init_weight_mean': 0.0, 'init_weight_stddev': 0.01,
        'init_bias_mean': 0.0, 'init_bias_stddev': 0.01
    },
    {
        'n_nodes': 2, 'activation': tf.identity, 'init_weight_mean': 0.0, 'init_weight_stddev': 0.01,
        'init_bias_mean': 0.0, 'init_bias_stddev': 0.01
    },
    {
        'n_nodes': 64, 'activation': tf.tanh, 'init_weight_mean': 0.0, 'init_weight_stddev': 0.01,
        'init_bias_mean': 0.0, 'init_bias_stddev': 0.01
    },
    {
        'n_nodes': 64, 'activation': tf.tanh, 'init_weight_mean': 0.0, 'init_weight_stddev': 0.01,
        'init_bias_mean': 0.0, 'init_bias_stddev': 0.01
    },
    {
        'n_nodes': 64, 'activation': tf.tanh, 'init_weight_mean': 0.0, 'init_weight_stddev': 0.01,
        'init_bias_mean': 0.0, 'init_bias_stddev': 0.01
    },
    {
        'n_nodes': 784, 'activation': tf.identity, 'init_weight_mean': 0.0, 'init_weight_stddev': 0.01,
        'init_bias_mean': 0.0, 'init_bias_stddev': 0.01
    }
]

In [154]:
monitors = [LossMonitor(200)]

In [155]:
ffnn = FFNN(
    lc, monitors=monitors, optimizer=tf.train.AdamOptimizer(), input_vector=pipe_out[0], train_targets_vector=pipe_out[1]
)
ffnn.init_session()

In [156]:
%%time
for epoch in range(100):
    ffnn.session.run(iterator.initializer)
    ffnn.train_online()

CPU times: user 2h 40min 35s, sys: 1h 39s, total: 3h 41min 14s
Wall time: 3h 5min 26s


In [157]:
plotly.iplot(ffnn.monitors[0].plot())

In [158]:
inp = tf.placeholder(tf.float32, shape=(None, 784))
outp = inp
for i in range(4):
    w = ffnn.weights[i]
    b = ffnn.biases[i]
    a = ffnn.activation[i]
    outp = a(tf.matmul(outp, w) + b)
    

outp = ffnn.session.run(outp, feed_dict={inp: train_in[:20000]})

In [159]:
figure = go.Figure(
    data=[
        go.Scattergl(
            x=outp[train_labels.argmax(axis=1)[:20000] == i, 0],
            y=outp[train_labels.argmax(axis=1)[:20000] == i, 1],
            mode='markers',
            marker={'size': 2, 'opacity': 1},
            name='{}'.format(i)
        )
        for i in range(10)
    ]
)

plotly.iplot(figure)

# Feed Forwards Autoencoder w/ Dist Mat Loss

In [10]:
d = tf.data.Dataset.from_tensor_slices((train_in, train_in))
d = d.repeat(50)
d = d.batch(300)
iterator = d.make_initializable_iterator()
pipe_out = iterator.get_next()

In [4]:
def compute_pdist_mat(A):
    r = tf.reduce_sum(A*A, 1)
    r = tf.reshape(r, [-1, 1])
    D = r - 2*tf.matmul(A, tf.transpose(A)) + tf.transpose(r)
    return D

def compute_knn_mat(A):
    D = compute_pdist_math(A)
    

In [130]:
class FFAutoencoder(NN):
    def create_params(self):
        self.activation = [lc['activation'] for lc in self.lc[1:]]
        self.weights = []
        self.biases = []

        n_nodes_prev_layer = self.lc[0]
        for i in range(len(self.lc) - 1):
            lc = self.lc[i + 1]

            weights = tf.Variable(tf.random_normal(
                shape=[n_nodes_prev_layer, lc['n_nodes']],
                mean=lc['init_weight_mean'],
                stddev=lc['init_weight_stddev'],
                dtype=self.float_type
            ))
            self.weights.append(weights)

            bias = tf.Variable(tf.random_normal(
                shape=[lc['n_nodes']],
                mean=lc['init_bias_mean'],
                stddev=lc['init_bias_stddev'],
                dtype=self.float_type
            ))
            self.biases.append(bias)

            n_nodes_prev_layer = lc['n_nodes']

    def feed_forwards(self, input_vector, n=None):
        if n is None:
            n = len(self.lc)
            
        for w, b, a in zip(self.weights[:n], self.biases[:n], self.activation[:n]):
            input_vector = a(tf.matmul(input_vector, w) + b)
        return input_vector

    def create_train_step(self, weight=0.95):
        n = 4
        embedded_points = self.feed_forwards(self.input, n)
        batch_input_dmat = compute_pdist_mat(self.input)
        batch_output_dmat = compute_pdist_mat(embedded_points)
        
        main_loss_val = self.loss_func(self.output, self.train_targets)
        dmat_loss_val = tf.reduce_mean((batch_input_dmat - batch_output_dmat) ** 2)
        
        self.loss_val = weight * main_loss_val + (1 - weight) * dmat_loss_val
        self.train_step = self.optimizer.minimize(self.loss_val)

In [131]:
lc = [
    784,
    {
        'n_nodes': 64, 'activation': tf.tanh, 'init_weight_mean': 0.0, 'init_weight_stddev': 0.01,
        'init_bias_mean': 0.0, 'init_bias_stddev': 0.01
    },
    {
        'n_nodes': 64, 'activation': tf.tanh, 'init_weight_mean': 0.0, 'init_weight_stddev': 0.01,
        'init_bias_mean': 0.0, 'init_bias_stddev': 0.01
    },
    {
        'n_nodes': 64, 'activation': tf.tanh, 'init_weight_mean': 0.0, 'init_weight_stddev': 0.01,
        'init_bias_mean': 0.0, 'init_bias_stddev': 0.01
    },
    {
        'n_nodes': 2, 'activation': tf.identity, 'init_weight_mean': 0.0, 'init_weight_stddev': 0.01,
        'init_bias_mean': 0.0, 'init_bias_stddev': 0.01
    },
    {
        'n_nodes': 64, 'activation': tf.tanh, 'init_weight_mean': 0.0, 'init_weight_stddev': 0.01,
        'init_bias_mean': 0.0, 'init_bias_stddev': 0.01
    },
    {
        'n_nodes': 64, 'activation': tf.tanh, 'init_weight_mean': 0.0, 'init_weight_stddev': 0.01,
        'init_bias_mean': 0.0, 'init_bias_stddev': 0.01
    },
    {
        'n_nodes': 64, 'activation': tf.tanh, 'init_weight_mean': 0.0, 'init_weight_stddev': 0.01,
        'init_bias_mean': 0.0, 'init_bias_stddev': 0.01
    },
    {
        'n_nodes': 784, 'activation': tf.identity, 'init_weight_mean': 0.0, 'init_weight_stddev': 0.01,
        'init_bias_mean': 0.0, 'init_bias_stddev': 0.01
    }
]

In [132]:
monitors = [LossMonitor(200)]

In [133]:
ffa = FFAutoencoder(
    lc, monitors=monitors, optimizer=tf.train.AdamOptimizer(), input_vector=pipe_out[0], train_targets_vector=pipe_out[1]
)
ffa.init_session()

In [138]:
%%time
for epoch in range(50):
    ffa.session.run(iterator.initializer)
    ffa.train_online()

CPU times: user 2h 16min 22s, sys: 37min 58s, total: 2h 54min 20s
Wall time: 1h 50min 8s


In [139]:
plotly.iplot(ffa.monitors[0].plot())

In [140]:
inp = tf.placeholder(tf.float32, shape=(None, 784))
outp = inp
for i in range(4):
    w = ffa.weights[i]
    b = ffa.biases[i]
    a = ffa.activation[i]
    outp = a(tf.matmul(outp, w) + b)
    

outp = ffa.session.run(outp, feed_dict={inp: train_in[:20000]})

In [141]:
figure = go.Figure(
    data=[
        go.Scattergl(
            x=outp[train_labels.argmax(axis=1)[:20000] == i, 0],
            y=outp[train_labels.argmax(axis=1)[:20000] == i, 1],
            mode='markers',
            marker={'size': 2, 'opacity': 1},
            name='{}'.format(i)
        )
        for i in range(10)
    ]
)

plotly.iplot(figure)

In [149]:
a = tf.constant(np.array([float('inf'), 1]))

In [151]:
tf.Session().run(tf.reduce_sum(a - a))

nan